In [1]:
using Pkg
using JuMP
using Gurobi
#using GLPK
using XLSX
using DataFrames

In [2]:
using LinearAlgebra

In [3]:
shared_cand = DataFrame(XLSX.readtable("CandLine.xlsx", "Taul1", header=true)...) #Dataframe of shared candidate lines
int_cand =  DataFrame(XLSX.readtable("CandLineInt.xlsx", "Taul1", header=true)...) #Dataframe of internal candidate lines
shared_ex =  DataFrame(XLSX.readtable("SharedEline.xlsx", "Taul1", header=true)...) #Dataframe of shared existing lines
int_ex = DataFrame(XLSX.readtable("Tran.xlsx", "Taul1", header=true)...) #Dataframe of internal existing lines
gen =  DataFrame(XLSX.readtable("Gen.xlsx" , "Taul1", header=true)...) #Dataframe of generators
load =  DataFrame(XLSX.readtable("Load.xlsx", "Taul1", header=true)...) #Dataframe of loads
##An example of the load dataframe can be found as follows

35×6 DataFrame
 Row │ zoneNum  lNodeID  P_load1  P_load2  P_load3  P_load4 
     │ Any      Any      Any      Any      Any      Any     
─────┼──────────────────────────────────────────────────────
   1 │ 1        2        -21.7    -10.85   -16.275  -5.425
   2 │ 1        3        -94.2    -47.1    -70.65   -23.55
   3 │ 1        4        -47.8    -23.9    -35.85   -11.95
   4 │ 1        5        -7.6     -3.8     -5.7     -1.9
   5 │ 1        6        -11.2    -5.6     -8.4     -2.8
   6 │ 1        9        -29.5    -14.75   -22.125  -7.375
   7 │ 1        10       -9       -4.5     -6.75    -2.25
   8 │ 1        11       -3.5     -1.75    -2.625   -0.875
   9 │ 1        12       -6.1     -3.05    -4.575   -1.525
  10 │ 1        13       -13.5    -6.75    -10.125  -3.375
  11 │ 1        14       -14.9    -7.45    -11.175  -3.725
  ⋮  │    ⋮        ⋮        ⋮        ⋮        ⋮        ⋮
  26 │ 2        21       -17.5    -8.75    -13.125  -4.375
  27 │ 2        23       -3.2     -1.6     -2.4     -0.8
  28 │ 2        24       -8.7     -4.35    -6.525   -2.175
  29 │ 2        26       -3.5     -1.75    -2.625   -0.875
  30 │ 2        29       -2.4     -1.2     -1.8     -0.6
  31 │ 2        30       -10.6    -5.3     -7.95    -2.65
  32 │ 3        2        -20      -10      -15      -5
  33 │ 3        3        -45      -22.5    -33.75   -11.25
  34 │ 3        4        -40      -20      -30      -10
  35 │ 3        5        -60      -30      -45      -15
                                             14 rows omitted

In [4]:
cand_from(i) = (shared_cand.nodeZone1 .== i)
cand_to(i) = (shared_cand.nodeZone2 .== i)
ex_from(i) = (shared_ex.nodeZone1 .== i)
ex_to(i) = (shared_ex.nodeZone2 .== i)

ex_to (generic function with 1 method)

In [5]:
l(i) = load[load.zoneNum .== i, :] # load within zone i
g(i) = gen[gen.zoneNum .== i, :]   # generators within zone i
shared_c(i) = vcat(shared_cand[shared_cand.nodeZone1 .== i,:] , shared_cand[shared_cand.nodeZone2 .== i, :]) #shared candidate lines within zone i
int_c(i) = int_cand[int_cand.zoneNum .== i, :]   # number of internal candidate lines within zone i
shared_e(i) = vcat(shared_ex[shared_ex.nodeZone1 .== i,:] , shared_ex[shared_ex.nodeZone2 .== i, :]) #shared existing lines within zone i
int_e(i) =int_ex[int_ex.zoneNum .== i, :]       # internal existing lines within zone i
MC(i) = (g(i).C2 .* (g(i).PgMax .^ 2) .+ g(i).C1 .* g(i).PgMax .- g(i).C2 .*(g(i).PgMin .^ 2) .- g(i).C1 .* g(i).PgMin) ./ (g(i).PgMax .- g(i).PgMin) #Marginal cost of generators within zone i
bin_c(i) = (shared_cand.nodeZone1 .== i) + (shared_cand.nodeZone2 .== i) # A binary vector through which we can check if the shared candidate lines belong to zone i
bin_e(i) = (shared_ex.nodeZone1 .== i) + (shared_ex.nodeZone2 .== i) # A binary vector through which we can check if the shared existing lines belong to zone i

bin_e (generic function with 1 method)

In [6]:
m(i) = setdiff([1,2,3], [i])

m (generic function with 1 method)

In [7]:
function zonal_app(i, N, cand_lambda, ex_lambda,shared_line_decision_var, int_line_decision_var,
        shared_cand_angle_self, shared_ex_angle_self, shared_cand_angle_1, shared_ex_angle_1, 
        shared_cand_angle_2, shared_ex_angle_2)
    
    Mod4 = Model(Gurobi.Optimizer)
    
    
    @variable(Mod4,0 <= gen_var[1:N]) # generation at each node
    @variable(Mod4,shared_cand_flow[1:nrow(shared_cand)])  #Power flowing into shared candidate lines 
    @variable(Mod4,int_cand_flow[1:nrow(int_c(i))]) #Power flowing into internal candidate lines 
    @variable(Mod4,0 <= shared_cand_angle[1:nrow(shared_cand),1:2]<= 2*pi) #Phase angle decision for shared candidate lines
    @variable(Mod4,0 <= int_cand_angle[1:nrow(int_c(i)),1:2]<= 2*pi) #Phase angle decision for internal candidate lines
    @variable(Mod4,shared_ex_flow[1:nrow(shared_ex)])  #Power flowing on shared existing shared lines
    @variable(Mod4,int_ex_flow[1:nrow(int_e(i))])  #Power flowing on internal existing lines
    @variable(Mod4,0 <= shared_ex_angle[1:nrow(shared_ex),1:2]<= 2*pi) #Phase angle for existing shared lines
    @variable(Mod4,0 <= int_ex_angle[1:nrow(int_e(i)),1:2]<= 2*pi) #Phase angle for internal existing lines
    
    omega = 0.36;
    eta = 0.6;
    
    @expression(Mod4, total_cost, sum((gen_var[n] .* sum((g(i).gNodeID .== n) .* MC(i))) for n in 1:N)
        .+ sum(sum(eta * shared_ex_angle[h,1] .* (shared_ex_angle_self[h,1] .- shared_ex_angle_1[h,1]) .+
            eta * shared_ex_angle[h,1] .* (shared_ex_angle_self[h,1] .- shared_ex_angle_2[h,1]) .+
            eta * shared_ex_angle[h,2] .* (shared_ex_angle_self[h,2] .- shared_ex_angle_1[h,2]) .+
            eta * shared_ex_angle[h,2] .* (shared_ex_angle_self[h,2] .- shared_ex_angle_2[h,2]) .+
            shared_ex_angle[h,1] .* ex_lambda[h,1] .+ 
            shared_ex_angle[h,2] .* ex_lambda[h,2] for h in 1:nrow(shared_ex))) .+
            sum(sum((omega /2) * (shared_ex_angle[:,1] .- shared_ex_angle_self[:,1]) .^ 2)) .+
            sum(sum((omega /2) * (shared_ex_angle[:,2] .- shared_ex_angle_self[:,2]) .^ 2))
        .+ sum(sum(eta * shared_cand_angle[c,1] .* (shared_cand_angle_self[c,1] .- shared_cand_angle_1[c,1]) .+
            eta * shared_cand_angle[c,1] .* (shared_cand_angle_self[c,1] .- shared_cand_angle_2[c,1]) .+
            eta * shared_cand_angle[c,2] .* (shared_cand_angle_self[c,2] .- shared_cand_angle_1[c,2]) .+
            eta * shared_cand_angle[c,2] .* (shared_cand_angle_self[c,2] .- shared_cand_angle_2[c,2]) .+
            shared_cand_angle[c,1] .* cand_lambda[c,1] .+ 
            shared_cand_angle[c,2] .* cand_lambda[c,2] for c in 1:nrow(shared_cand))) .+
            sum(sum((omega /2) * (shared_cand_angle[:,1] .- shared_cand_angle_self[:,1]) .^ 2)) .+
            sum(sum((omega /2) * (shared_cand_angle[:,2] .- shared_cand_angle_self[:,2]) .^ 2)))
            
            
            
            
    for n in 1:N
        # Power balance constraint for each node
        @constraint(Mod4, sum(g(i).gNodeID .== n) .* gen_var[n] .+ sum(l(i).P_load1 .* (l(i).lNodeID .== n)) .==
            sum((shared_cand.tNodeID1 .== n) .*bin_c(i) .* shared_cand_flow) .- sum((shared_cand.tNodeID2 .== n) .* bin_c(i) .* shared_cand_flow) .+
            sum((shared_ex.tNodeID1 .== n) .* bin_e(i) .* shared_ex_flow) .- sum((shared_ex.tNodeID2 .== n) .* bin_e(i) .* shared_ex_flow) .+
            sum((int_c(i).tNodeID1 .== n) .* int_cand_flow) .- sum((int_c(i).tNodeID2 .== n) .* int_cand_flow) .+
            sum((int_e(i).tNodeID1 .== n) .* int_ex_flow) .- sum((int_e(i).tNodeID2 .== n) .* int_ex_flow))
        #Lower limit for generation of each node
        @constraint(Mod4, sum(g(i).gNodeID .== n) .* gen_var[n] .<= sum((g(i).gNodeID .== n) .* g(i).PgMax))
        #Upper limit for generation of each node
        @constraint(Mod4, sum((g(i).gNodeID .== n) .* g(i).PgMin) .<= sum(g(i).gNodeID .== n) .* gen_var[n])
    end
    
    M=1000 #Big number
    
    #Constraints elated to the candidate shared lines:
    for c in 1:nrow(shared_cand) 
        #Associating the power flowing within the line with the phase angles of nodes:
        @constraint(Mod4,-M .* (1 .- bin_c(i) .* shared_line_decision_var[c]) .<= bin_c(i) .* shared_cand_flow[c] .- ((1 ./ shared_cand.reacT[c]) .* (bin_c(i) .* shared_cand_angle[c,1] .- bin_c(i) .* shared_cand_angle[c,2])))
        
        @constraint(Mod4, bin_c(i) .* shared_cand_flow[c] .- ((1 ./ shared_cand.reacT[c]) .* (bin_c(i) .* shared_cand_angle[c,1] .- bin_c(i) .* shared_cand_angle[c,2])) .<= M .* (1 .- bin_c(i) .* shared_line_decision_var[c]))
        #limiting the upper bound of power flow flowing within candidate shared lines
        @constraint(Mod4, bin_c(i) .* shared_cand_flow[c] .<= bin_c(i) .* shared_line_decision_var[c] .* shared_cand.ptMax[c])
        #Limiting the lower bound of power flowing within the candidate shared lines
        @constraint(Mod4, -shared_cand.ptMax[c] .* bin_c(i) .* shared_line_decision_var[c] .<= bin_c(i) .* shared_cand_flow[c])
        @constraint(Mod4, shared_cand_angle[5,2] .== 0)
    end
    
    #The same constraints related to the candidate internal lines:
    for c in 1:nrow(int_c(i))
        @constraint(Mod4,-M .* (1 .- int_line_decision_var[c]) .<= int_cand_flow[c] .- ((1 ./ int_c(i).reacT[c]) .* (int_cand_angle[c,1] .- int_cand_angle[c,2])))
        @constraint(Mod4, int_cand_flow[c] .- ((1 ./ int_c(i).reacT[c]) .* (int_cand_angle[c,1] .- int_cand_angle[c,2])) .<= M .* (1 .- int_line_decision_var[c]))
        @constraint(Mod4, int_cand_flow[c] .<= int_line_decision_var[c] .* int_c(i).ptMax[c])
        @constraint(Mod4, -int_c(i).ptMax[c] .*int_line_decision_var[c] .<= int_cand_flow[c])
    end
    
    #The same constraints related to the shared existing lines:
    for h in 1:nrow(shared_ex)
        @constraint(Mod4, bin_e(i) .* shared_ex_flow[h] .== (1 ./ shared_ex.reacT[h]) .* (bin_e(i) .* shared_ex_angle[h,1] .- bin_e(i) .* shared_ex_angle[h,2]))
        @constraint(Mod4, bin_e(i) .* shared_ex_flow[h] .<= bin_e(i) .* shared_ex. ptMax[h])
        @constraint(Mod4, bin_e(i) .* -shared_ex.ptMax[h] .<= bin_e(i) .* shared_ex_flow[h])
        @constraint(Mod4, shared_ex_angle[1,2] .== 0)
        @constraint(Mod4, shared_ex_angle[7,2] .== 0)

    end
    #The same constraints related to the internal existing lines:
    
    for h in 1:nrow(int_e(i))
        @constraint(Mod4, int_ex_flow[h] .== (1 ./ int_e(i).reacT[h]) .* (int_ex_angle[h,1] .- int_ex_angle[h,2]))
        @constraint(Mod4, int_ex_flow[h] .<= int_e(i).ptMax[h])
        @constraint(Mod4, -int_e(i).ptMax[h] .<= int_ex_flow[h])
    end
    
    #The model objective is to minimize the total cost:
    
    @objective(Mod4, Min, total_cost)
    optimize!(Mod4)
    if termination_status(Mod4) == MOI.OPTIMAL #If the solution is optimal then it returns the variables
    
        shared_cand_power = value.(shared_cand_flow)
        shared_cand_phase_angle = value.(shared_cand_angle)
        shared_ex_power = value.(shared_ex_flow)
        shared_ex_phase_angle = value.(shared_ex_angle)
        gen_power = value.(gen_var)
        int_cand_power = value.(int_cand_flow)
        int_cand_phase_angle = value.(int_cand_angle)
        obj_value = objective_value(Mod4)
        [obj_value, shared_cand_power,shared_cand_phase_angle,shared_ex_power,shared_ex_phase_angle,gen_power, int_cand_power, int_cand_phase_angle]

    end
end
    
    

zonal_app (generic function with 1 method)

In [8]:
f=ones(12000)
cand_lambda_1= zeros(12000,nrow(shared_cand),2)
ex_lambda_1 = zeros(12000,nrow(shared_ex),2)
cand_lambda_2= zeros(12000,nrow(shared_cand),2)
ex_lambda_2 = zeros(12000,nrow(shared_ex),2)
cand_lambda_3= zeros(12000,nrow(shared_cand),2)
ex_lambda_3 = zeros(12000,nrow(shared_ex),2)
cand_angle_1 = zeros(12000,nrow(shared_cand),2)
c_angle_1 = zeros(12000,nrow(shared_cand),2)
cand_angle_2 = zeros(12000,nrow(shared_cand),2)
c_angle_2 = zeros(12000,nrow(shared_cand),2)
cand_angle_3 = zeros(12000,nrow(shared_cand),2)
c_angle_3 = zeros(12000,nrow(shared_cand),2)

ex_angle_1 = zeros(12000,nrow(shared_ex),2)
e_angle_1 = zeros(12000,nrow(shared_ex),2)
ex_angle_2 = zeros(12000,nrow(shared_ex),2)
e_angle_2 = zeros(12000,nrow(shared_ex),2)
ex_angle_3 = zeros(12000,nrow(shared_ex),2)
e_angle_3 = zeros(12000,nrow(shared_ex),2)

cand_flow_1 =zeros(12000,nrow(shared_cand))
cand_flow_2 =zeros(12000,nrow(shared_cand))
cand_flow_3 =zeros(12000,nrow(shared_cand))
ex_flow_1 = zeros(12000,nrow(shared_ex))
ex_flow_2 = zeros(12000,nrow(shared_ex))
ex_flow_3 = zeros(12000,nrow(shared_ex))



shared_line_decision_var_m =  
[0.0
 0.0
 0.0
 1.0
 1.0
 1.0]
int_line_decision_var_1 =
[ 0.0
 1.0
 1.0
 0.0
 1.0
 1.0
 0.0
 0.0
 0.0
 1.0]
int_line_decision_var_2 =
[1.0
 0.0
 0.0
 0.0
 0.0
 1.0
 1.0
 0.0
 0.0
 1.0
 1.0
 0.0
 0.0
 0.0
 1.0
 0.0
 0.0
 0.0]
int_line_decision_var_3 =
[0.0
 0.0]

2-element Vector{Float64}:
 0.0
 0.0

In [9]:
    j = 2
    for j in 2:500    # It considers 1000 iteration
        if abs(f[j-1]) > 0.00000001  
         
            R_1 = zonal_app(1, 14, cand_lambda_1[j,:,:], ex_lambda_1[j,:,:],shared_line_decision_var_m, int_line_decision_var_1,
            cand_angle_1[j-1,:,:], ex_angle_1[j-1,:,:], cand_angle_2[j-1,:,:],  ex_angle_2[j-1,:,:], 
            cand_angle_3[j-1,:,:], ex_angle_3[j-1,:,:])
        
            R_2 = zonal_app(2, 30, cand_lambda_2[j,:,:], ex_lambda_2[j,:,:],shared_line_decision_var_m, int_line_decision_var_2,
            cand_angle_2[j-1,:,:], ex_angle_2[j-1,:,:], cand_angle_1[j-1,:,:], ex_angle_1[j-1,:,:], 
            cand_angle_3[j-1,:,:], ex_angle_3[j-1,:,:])       
        
            R_3 = zonal_app(3, 5, cand_lambda_3[j,:,:], ex_lambda_3[j,:,:],shared_line_decision_var_m, int_line_decision_var_3,
            cand_angle_3[j-1,:,:], ex_angle_3[j-1,:,:], cand_angle_1[j-1,:,:],  ex_angle_1[j-1,:,:], 
            cand_angle_2[j-1,:,:], ex_angle_2[j-1,:,:])
        
        
            cand_lambda_1[j+1,:,:] .= cand_lambda_1[j,:,:] .+ 0.1 * (R_1[3] .- (R_2[3] .+ R_3[3]) ./2)
            cand_lambda_2[j+1,:,:] .= cand_lambda_2[j,:,:] .+ 0.1 * (R_2[3] .- (R_1[3] .+ R_3[3]) ./2)
            cand_lambda_3[j+1,:,:] .= cand_lambda_3[j,:,:] .+ 0.1 * (R_3[3] .- (R_1[3] .+ R_2[3]) ./2)
        
        
    
            ex_lambda_1[j+1,:,:] .= ex_lambda_1[j,:,:] .+ 0.1 * (R_1[5] .- (R_2[5] .+ R_3[5]) ./2)
            ex_lambda_2[j+1,:,:] .= ex_lambda_2[j,:,:] .+ 0.1 * (R_2[5] .- (R_1[5] .+ R_3[5]) ./2)
            ex_lambda_3[j+1,:,:] .= ex_lambda_3[j,:,:] .+ 0.1 * (R_3[5] .- (R_1[5] .+ R_2[5]) ./2)
        
            f[j] = sum(sum((R_1[3] .- (R_2[3]./2 .+ R_3[3]./2)).^ 2)) +
                    sum(sum((R_2[3] .- (R_1[3]./2 .+ R_3[3]./2)).^ 2)) +
                    sum(sum((R_3[3] .- (R_1[3]./2 .+ R_2[3]./2)).^ 2)) +
                    sum(sum((R_1[5] .- (R_2[5]./2 .+ R_3[5]./2)).^ 2)) +
                    sum(sum((R_2[5] .- (R_1[5]./2 .+ R_3[5]./2)).^ 2)) +
                    sum(sum((R_3[5] .- (R_2[5]./2 .+ R_1[5]./2)).^ 2))
        
            c_angle_1 = R_1[3]
            c_angle_2 = R_2[3]
            c_angle_3 = R_3[3]
        
            e_angle_1 = R_1[5]
            e_angle_2 = R_2[5]
            e_angle_3 = R_3[5]
            
            cand_flow_1 = R_1[2]
            cand_flow_2 = R_2[2]
            cand_flow_3 = R_3[2]
        
            ex_flow_1 = R_1[4]
            ex_flow_2 = R_2[4]
            ex_flow_3 = R_3[4]
            
            
            h= R_2[1] + R_1[1] + R_3[1]
            
            if isdefined(Main, :IJulia)
                Main.IJulia.stdio_bytes[] = 0
            end
        
            print('*') 
        
        else
            print(c_angle_1)
            print(c_angle_2)
            print(c_angle_3)
            print(e_angle_1)
            print(e_angle_2)
            print(e_angle_3)
        end
    end
    

Academic license - for non-commercial use only - expires 2023-06-28
Gurobi Optimizer version 9.1.2 build v9.1.2rc0 (win64)
Thread count: 4 physical cores, 4 logical processors, using up to 4 threads
Optimize a model with 500 rows, 146 columns and 674 nonzeros
Model fingerprint: 0xebee9342
Model has 28 quadratic objective terms
Coefficient statistics:
  Matrix range     [1e+00, 2e+01]
  Objective range  [3e+01, 6e+01]
  QObjective range [4e-01, 4e-01]
  Bounds range     [6e+00, 6e+00]
  RHS range        [4e+00, 1e+03]
Presolve removed 488 rows and 115 columns
Presolve time: 0.00s
Presolved: 12 rows, 31 columns, 57 nonzeros
Presolved model has 7 quadratic objective terms
Ordering time: 0.00s

Barrier statistics:
 AA' NZ     : 2.300e+01
 Factor NZ  : 7.800e+01
 Factor Ops : 6.500e+02 (less than 1 second per iteration)
 Threads    : 1

                  Objective                Residual
Iter       Primal          Dual         Primal    Dual     Compl     Time
   0   2.81557726e+06 -1.62656

*Academic license - for non-commercial use only - expires 2023-06-28
Gurobi Optimizer version 9.1.2 build v9.1.2rc0 (win64)
Thread count: 4 physical cores, 4 logical processors, using up to 4 threads
Optimize a model with 500 rows, 146 columns and 674 nonzeros
Model fingerprint: 0x574948bf
Model has 28 quadratic objective terms
Coefficient statistics:
  Matrix range     [1e+00, 2e+01]
  Objective range  [3e-05, 6e+01]
  QObjective range [4e-01, 4e-01]
  Bounds range     [6e+00, 6e+00]
  RHS range        [4e+00, 1e+03]
Presolve removed 488 rows and 115 columns
Presolve time: 0.00s
Presolved: 12 rows, 31 columns, 57 nonzeros
Presolved model has 7 quadratic objective terms
Ordering time: 0.00s

Barrier statistics:
 AA' NZ     : 2.300e+01
 Factor NZ  : 7.800e+01
 Factor Ops : 6.500e+02 (less than 1 second per iteration)
 Threads    : 1

                  Objective                Residual
Iter       Primal          Dual         Primal    Dual     Compl     Time
   0   2.81794099e+06 -1.6265

*Academic license - for non-commercial use only - expires 2023-06-28
Gurobi Optimizer version 9.1.2 build v9.1.2rc0 (win64)
Thread count: 4 physical cores, 4 logical processors, using up to 4 threads
Optimize a model with 500 rows, 146 columns and 674 nonzeros
Model fingerprint: 0x93745782
Model has 28 quadratic objective terms
Coefficient statistics:
  Matrix range     [1e+00, 2e+01]
  Objective range  [4e-05, 6e+01]
  QObjective range [4e-01, 4e-01]
  Bounds range     [6e+00, 6e+00]
  RHS range        [4e+00, 1e+03]
Presolve removed 488 rows and 115 columns
Presolve time: 0.00s
Presolved: 12 rows, 31 columns, 57 nonzeros
Presolved model has 7 quadratic objective terms
Ordering time: 0.00s

Barrier statistics:
 AA' NZ     : 2.300e+01
 Factor NZ  : 7.800e+01
 Factor Ops : 6.500e+02 (less than 1 second per iteration)
 Threads    : 1

                  Objective                Residual
Iter       Primal          Dual         Primal    Dual     Compl     Time
   0   2.81901979e+06 -1.6265

*Academic license - for non-commercial use only - expires 2023-06-28
Gurobi Optimizer version 9.1.2 build v9.1.2rc0 (win64)
Thread count: 4 physical cores, 4 logical processors, using up to 4 threads
Optimize a model with 500 rows, 146 columns and 674 nonzeros
Model fingerprint: 0x53466e82
Model has 28 quadratic objective terms
Coefficient statistics:
  Matrix range     [1e+00, 2e+01]
  Objective range  [3e-05, 6e+01]
  QObjective range [4e-01, 4e-01]
  Bounds range     [6e+00, 6e+00]
  RHS range        [4e+00, 1e+03]
Presolve removed 488 rows and 115 columns
Presolve time: 0.00s
Presolved: 12 rows, 31 columns, 57 nonzeros
Presolved model has 7 quadratic objective terms
Ordering time: 0.00s

Barrier statistics:
 AA' NZ     : 2.300e+01
 Factor NZ  : 7.800e+01
 Factor Ops : 6.500e+02 (less than 1 second per iteration)
 Threads    : 1

                  Objective                Residual
Iter       Primal          Dual         Primal    Dual     Compl     Time
   0   2.81981946e+06 -1.6265

*Academic license - for non-commercial use only - expires 2023-06-28
Gurobi Optimizer version 9.1.2 build v9.1.2rc0 (win64)
Thread count: 4 physical cores, 4 logical processors, using up to 4 threads
Optimize a model with 500 rows, 146 columns and 674 nonzeros
Model fingerprint: 0xc1810f16
Model has 28 quadratic objective terms
Coefficient statistics:
  Matrix range     [1e+00, 2e+01]
  Objective range  [3e-05, 6e+01]
  QObjective range [4e-01, 4e-01]
  Bounds range     [6e+00, 6e+00]
  RHS range        [4e+00, 1e+03]
Presolve removed 488 rows and 115 columns
Presolve time: 0.00s
Presolved: 12 rows, 31 columns, 57 nonzeros
Presolved model has 7 quadratic objective terms
Ordering time: 0.00s

Barrier statistics:
 AA' NZ     : 2.300e+01
 Factor NZ  : 7.800e+01
 Factor Ops : 6.500e+02 (less than 1 second per iteration)
 Threads    : 1

                  Objective                Residual
Iter       Primal          Dual         Primal    Dual     Compl     Time
   0   2.82041234e+06 -1.6265

...

*Academic license - for non-commercial use only - expires 2023-06-28
Gurobi Optimizer version 9.1.2 build v9.1.2rc0 (win64)
Thread count: 4 physical cores, 4 logical processors, using up to 4 threads
Optimize a model with 500 rows, 146 columns and 674 nonzeros
Model fingerprint: 0x837311cd
Model has 28 quadratic objective terms
Coefficient statistics:
  Matrix range     [1e+00, 2e+01]
  Objective range  [2e-06, 6e+01]
  QObjective range [4e-01, 4e-01]
  Bounds range     [6e+00, 6e+00]
  RHS range        [4e+00, 1e+03]
Presolve removed 488 rows and 115 columns
Presolve time: 0.00s
Presolved: 12 rows, 31 columns, 57 nonzeros
Presolved model has 7 quadratic objective terms
Ordering time: 0.00s

Barrier statistics:
 AA' NZ     : 2.300e+01
 Factor NZ  : 7.800e+01
 Factor Ops : 6.500e+02 (less than 1 second per iteration)
 Threads    : 1

                  Objective                Residual
Iter       Primal          Dual         Primal    Dual     Compl     Time
   0   2.82287404e+06 -1.6265

*Academic license - for non-commercial use only - expires 2023-06-28
Gurobi Optimizer version 9.1.2 build v9.1.2rc0 (win64)
Thread count: 4 physical cores, 4 logical processors, using up to 4 threads
Optimize a model with 500 rows, 146 columns and 674 nonzeros
Model fingerprint: 0xfaaed0c2
Model has 28 quadratic objective terms
Coefficient statistics:
  Matrix range     [1e+00, 2e+01]
  Objective range  [2e-06, 6e+01]
  QObjective range [4e-01, 4e-01]
  Bounds range     [6e+00, 6e+00]
  RHS range        [4e+00, 1e+03]
Presolve removed 488 rows and 115 columns
Presolve time: 0.00s
Presolved: 12 rows, 31 columns, 57 nonzeros
Presolved model has 7 quadratic objective terms
Ordering time: 0.00s

Barrier statistics:
 AA' NZ     : 2.300e+01
 Factor NZ  : 7.800e+01
 Factor Ops : 6.500e+02 (less than 1 second per iteration)
 Threads    : 1

                  Objective                Residual
Iter       Primal          Dual         Primal    Dual     Compl     Time
   0   2.82287419e+06 -1.6265

*Academic license - for non-commercial use only - expires 2023-06-28
Gurobi Optimizer version 9.1.2 build v9.1.2rc0 (win64)
Thread count: 4 physical cores, 4 logical processors, using up to 4 threads
Optimize a model with 500 rows, 146 columns and 674 nonzeros
Model fingerprint: 0xf010160c
Model has 28 quadratic objective terms
Coefficient statistics:
  Matrix range     [1e+00, 2e+01]
  Objective range  [2e-06, 6e+01]
  QObjective range [4e-01, 4e-01]
  Bounds range     [6e+00, 6e+00]
  RHS range        [4e+00, 1e+03]
Presolve removed 488 rows and 115 columns
Presolve time: 0.00s
Presolved: 12 rows, 31 columns, 57 nonzeros
Presolved model has 7 quadratic objective terms
Ordering time: 0.00s

Barrier statistics:
 AA' NZ     : 2.300e+01
 Factor NZ  : 7.800e+01
 Factor Ops : 6.500e+02 (less than 1 second per iteration)
 Threads    : 1

                  Objective                Residual
Iter       Primal          Dual         Primal    Dual     Compl     Time
   0   2.82287441e+06 -1.6265

*Academic license - for non-commercial use only - expires 2023-06-28
Gurobi Optimizer version 9.1.2 build v9.1.2rc0 (win64)
Thread count: 4 physical cores, 4 logical processors, using up to 4 threads
Optimize a model with 500 rows, 146 columns and 674 nonzeros
Model fingerprint: 0x087caa53
Model has 28 quadratic objective terms
Coefficient statistics:
  Matrix range     [1e+00, 2e+01]
  Objective range  [2e-06, 6e+01]
  QObjective range [4e-01, 4e-01]
  Bounds range     [6e+00, 6e+00]
  RHS range        [4e+00, 1e+03]
Presolve removed 488 rows and 115 columns
Presolve time: 0.00s
Presolved: 12 rows, 31 columns, 57 nonzeros
Presolved model has 7 quadratic objective terms
Ordering time: 0.00s

Barrier statistics:
 AA' NZ     : 2.300e+01
 Factor NZ  : 7.800e+01
 Factor Ops : 6.500e+02 (less than 1 second per iteration)
 Threads    : 1

                  Objective                Residual
Iter       Primal          Dual         Primal    Dual     Compl     Time
   0   2.82287455e+06 -1.6265

*Academic license - for non-commercial use only - expires 2023-06-28
Gurobi Optimizer version 9.1.2 build v9.1.2rc0 (win64)
Thread count: 4 physical cores, 4 logical processors, using up to 4 threads
Optimize a model with 500 rows, 146 columns and 674 nonzeros
Model fingerprint: 0x5ab36fdc
Model has 28 quadratic objective terms
Coefficient statistics:
  Matrix range     [1e+00, 2e+01]
  Objective range  [2e-06, 6e+01]
  QObjective range [4e-01, 4e-01]
  Bounds range     [6e+00, 6e+00]
  RHS range        [4e+00, 1e+03]
Presolve removed 488 rows and 115 columns
Presolve time: 0.00s
Presolved: 12 rows, 31 columns, 57 nonzeros
Presolved model has 7 quadratic objective terms
Ordering time: 0.00s

Barrier statistics:
 AA' NZ     : 2.300e+01
 Factor NZ  : 7.800e+01
 Factor Ops : 6.500e+02 (less than 1 second per iteration)
 Threads    : 1

                  Objective                Residual
Iter       Primal          Dual         Primal    Dual     Compl     Time
   0   2.82287469e+06 -1.6265

In [10]:
f[1000]

1.0

In [11]:
c_angle_1

6×2 Matrix{Float64}:
 0.0         0.0
 0.0         0.0
 0.0         0.0
 5.75        3.2761e-11
 4.57527     0.0
 6.36737e-6  4.35137

In [12]:
c_angle_2

6×2 Matrix{Float64}:
 0.0         0.0
 0.0         0.0
 0.0         0.0
 5.74999     2.09518e-5
 4.57527     0.0
 1.26038e-5  4.35137

In [13]:
c_angle_3

6×2 Matrix{Float64}:
 0.0          0.0
 0.0          0.0
 0.0          0.0
 5.74999      1.73342e-5
 4.57641      0.0
 8.61728e-11  4.35246

In [14]:
e_angle_3 

8×2 Matrix{Float64}:
 6.28318      0.0
 0.0          0.0
 0.0          0.0
 0.000365067  0.000373967
 4.63022      8.0944e-11
 3.78011      9.92257e-11
 0.000418103  0.0
 1.12423e-10  3.33647

In [15]:
e_angle_2

8×2 Matrix{Float64}:
 6.28317      0.0
 0.0          0.0
 0.0          0.0
 0.000365101  0.000374
 4.62707      0.00448895
 3.77917      1.25804e-5
 0.000418128  0.0
 1.35991e-5   3.33556

In [16]:
e_angle_1

8×2 Matrix{Float64}:
 6.28319      0.0
 0.0          0.0
 0.0          0.0
 0.00036514   0.000374039
 4.62293      0.0086234
 3.77917      6.35569e-6
 0.000418126  0.0
 6.88057e-6   3.33556

In [18]:
cand_flow_1

6-element Vector{Float64}:
   0.0
   0.0
   0.0
  99.999999999994
  27.695308936432703
 -25.051055408722505

In [19]:
cand_flow_2

6-element Vector{Float64}:
   0.0
   0.0
   0.0
  99.99949463654065
  27.695308936413316
 -25.0510195053364

In [20]:
cand_flow_3

6-element Vector{Float64}:
   0.0
   0.0
   0.0
  99.99958004333007
  27.702225055531414
 -25.057347866322456

In [21]:
ex_flow_1

8-element Vector{Float64}:
  23.27105669325145
   0.0
   0.0
  -1.6004599132602272e-5
  77.03351119658328
  18.895812821336733
   0.0038011476775905786
 -16.036319245640627

In [22]:
ex_flow_2

8-element Vector{Float64}:
  23.271004447031704
   0.0
   0.0
  -1.6005671780673224e-5
  77.1716027052195
  18.895781697818002
   0.0038011681163592215
 -16.0362869448034

In [23]:
ex_flow_3

8-element Vector{Float64}:
  23.271030267842118
   0.0
   0.0
  -1.600747125407966e-5
  77.29914874664567
  18.900563301370177
   0.003800937521522601
 -16.04071503009298